In [8]:
import fitz
import base64
from io import BytesIO
from PIL import Image
from langchain_openai import ChatOpenAI
from langchain_core.messages import HumanMessage, SystemMessage

def convert_image_to_base64(image_bytes):
    """
    이미지 바이트를 base64 문자열로 변환
    """
    return base64.b64encode(image_bytes).decode('utf-8')

def classify_image_type(image_bytes):
    """
    GPT-4o를 사용하여 이미지가 그래프/도표인지 분류
    Returns:
        bool: True if image is graph/chart, False otherwise
    """
    llm = ChatOpenAI(model="gpt-4o", max_tokens=1000)
    base64_image = convert_image_to_base64(image_bytes)
    
    prompt = (
        "다음 이미지를 아래 두 가지 중 하나로 분류하세요:\n"
        "1. 그래프/도표\n"
        "2. 그외\n"
        "반드시 위 중 하나의 항목만 정확히 출력하세요."
    )
    
    messages = [
        SystemMessage(content="당신은 이미지 분류 전문 AI 에이전트입니다."),
        HumanMessage(content=[
            {"type": "text", "text": prompt},
            {"type": "image_url", "image_url": {"url": f"data:image/jpeg;base64,{base64_image}"}}
        ])
    ]
    
    response = llm.invoke(messages)
    label = response.content.strip()
    
    # 그래프/도표인 경우에만 True 반환
    return label == "그래프/도표"

def get_total_image_area_ratio(page, images):
    """
    페이지에서 감지된 모든 이미지의 총 면적 비율을 계산.
    """
    total_ratio = 0
    for img in images:
        xref = img[0]
        img_rects = page.get_image_rects(xref)
        if img_rects:
            x0, y0, x1, y1 = img_rects[0]
            img_width = x1 - x0
            img_height = y1 - y0
            img_area = img_width * img_height
            
            page_width, page_height = page.rect.width, page.rect.height
            page_area = page_width * page_height
            
            total_ratio += img_area / page_area
    
    return total_ratio

def should_interpret_image(image_bytes, total_area_ratio):
    """
    이미지 해석 여부를 결정하는 함수.
    Args:
        image_bytes: 이미지 바이트 데이터
        total_area_ratio (float): 페이지 내 모든 이미지의 총 면적 비율
    Returns:
        bool: 이미지를 해석해야 하면 True, 아니면 False
    """
    # 먼저 면적 비율 확인
    if total_area_ratio >= 0.6:
        return True
    
    # 면적 비율이 0.5 미만인 경우에만 LLM으로 그래프/도표 여부 확인
    is_graph_or_chart = classify_image_type(image_bytes)
    return is_graph_or_chart

def extract_page(pdf_path):
    """
    PDF에서 텍스트 및 이미지 정보를 추출.
    Returns:
        list: 각 페이지별 정보를 담은 딕셔너리 리스트
            - page: 페이지 번호 (1부터 시작)
            - text: 페이지에서 추출된 전체 텍스트
            - images: 이미지 정보 리스트
                - image: base64로 인코딩된 이미지
                - image_type: 이미지 해석 필요 여부 (bool)
    """
    doc = fitz.open(pdf_path)
    total_pages = len(doc)
    pdf_data = []

    for page_num in range(total_pages):
        page = doc[page_num]
        text = page.get_text("text")
        images = page.get_images(full=True)
        image_data = []

        # 페이지의 총 이미지 면적 비율 계산
        total_area_ratio = get_total_image_area_ratio(page, images)

        for img in images:
            xref = img[0]
            img_rects = page.get_image_rects(xref)
            
            if img_rects:
                # 이미지 추출
                pix = fitz.Pixmap(doc, xref)
                if pix.n > 4:  # CMYK를 RGB로 변환
                    pix = fitz.Pixmap(fitz.csRGB, pix)
                
                # 이미지를 바이트로 변환
                img_bytes = pix.tobytes()
                img_base64 = convert_image_to_base64(img_bytes)
                
                # 이미지 해석 여부 결정 (면적 비율 먼저 확인 후 필요시 LLM 사용)
                should_interpret = should_interpret_image(img_bytes, total_area_ratio)
                
                image_data.append({
                    "image": img_base64,
                    "image_type": should_interpret
                })
                
                pix = None  # 메모리 해제

        pdf_data.append({
            "page": page_num + 1,
            "text": text,
            "images": image_data
        })

    return pdf_data

def filter_important_images(pdf_data):
    """
    PDF 데이터에서 해석이 필요한 이미지(image_type이 True)만 필터링하여 반환
    페이지는 모두 유지하고 이미지만 필터링합니다.
    
    Args:
        pdf_data (list): extract_page 함수에서 반환된 PDF 데이터
    Returns:
        list: 필터링된 PDF 데이터 (모든 페이지 포함, 해석이 필요한 이미지만 포함)
    """
    filtered_data = []
    
    for page_info in pdf_data:
        # image_type이 True인 이미지만 필터링
        important_images = [img for img in page_info['images'] if img['image_type']]
        
        # 모든 페이지를 포함하되, 필터링된 이미지만 포함
        filtered_data.append({
            "page": page_info['page'],
            "text": page_info['text'],
            "images": important_images  # 빈 리스트가 될 수도 있음
        })
    
    return filtered_data

In [9]:
from dotenv import load_dotenv
load_dotenv()

# PDF 처리
pdf_path = "../../data/Presentation_Agent.pdf"
result = extract_page(pdf_path)

In [3]:
result

[{'page': 1,
  'text': 'Presentation Agent\n저희 발표 안합니다!\n정재식, 이진규\nㅈ소 기업\n',
  'images': []},
 {'page': 2,
  'text': '프로젝트 개요\n기획 배경\n프로젝트 소개\n01\nCONTENT\n프로젝트 기획\n자원 및 기술\n시스템 구조\n작업 흐름\n02\n프로젝트 방향성\n발전 방안\n03\n',
  'images': []},
 {'page': 3, 'text': '프로젝트 개요\n프로젝트 개요\n01\n', 'images': []},
 {'page': 4,
  'text': 'Wordcloud\nNetworkx\n01. 개요\n기획 배경\n“발표 준비”라는 키워드의 블로그, 뉴스, 카페, 지식인 등 에서\n제목 및 내용을 크롤링하여 수집\n발표는 우리 삶에 얼마나 밀접해 있을까?\n',
  'images': [{'image': '...',
    'image_type': True},
   {'image': '...',
    'image_type': True},
   {'image': '...',
    'image_type': True}]},
 {'page': 5,
  'text': '내성적 성격\n31.3%\n실수에 대한 압박감\n25%\n준비 부족\n14.6%\n무대 공포증\n12.5%\n질문의 대응이 어려워서\n10.4%\n시선에 대한 압박감\n01. 개요\n기획 배경\n취업포털 커리어넷에서 직장인 384명을 대상으로 한 설문조사\n타고난 내성적 성격 때문에\n발표 중에 실수하는 것이 \n두려워서\n무대 공포증이 있어서\n사람들과 시선을 마주치는\n것이 싫어서\n발표 전 불안감의 원인은 무엇일까?\n',
  'images': [{'image': '...',
    'image_type': False}]},
 {'page': 6,
  'text': '최초의 발표하는 인공지능 모델 : 오인용\n01. 개요\n프로젝트 소개\n중요한 내용을 중심으로 발표용 대본 생성\n

In [7]:
filtered_data = filter_important_images(result)
filtered_data

[{'page': 1,
  'text': 'Presentation Agent\n저희 발표 안합니다!\n정재식, 이진규\nㅈ소 기업\n',
  'images': []},
 {'page': 2,
  'text': '프로젝트 개요\n기획 배경\n프로젝트 소개\n01\nCONTENT\n프로젝트 기획\n자원 및 기술\n시스템 구조\n작업 흐름\n02\n프로젝트 방향성\n발전 방안\n03\n',
  'images': []},
 {'page': 3, 'text': '프로젝트 개요\n프로젝트 개요\n01\n', 'images': []},
 {'page': 4,
  'text': 'Wordcloud\nNetworkx\n01. 개요\n기획 배경\n“발표 준비”라는 키워드의 블로그, 뉴스, 카페, 지식인 등 에서\n제목 및 내용을 크롤링하여 수집\n발표는 우리 삶에 얼마나 밀접해 있을까?\n',
  'images': [{'image': '...',
    'image_type': True},
   {'image': '...',
    'image_type': True},
   {'image': '...',
    'image_type': True}]},
 {'page': 5,
  'text': '내성적 성격\n31.3%\n실수에 대한 압박감\n25%\n준비 부족\n14.6%\n무대 공포증\n12.5%\n질문의 대응이 어려워서\n10.4%\n시선에 대한 압박감\n01. 개요\n기획 배경\n취업포털 커리어넷에서 직장인 384명을 대상으로 한 설문조사\n타고난 내성적 성격 때문에\n발표 중에 실수하는 것이 \n두려워서\n무대 공포증이 있어서\n사람들과 시선을 마주치는\n것이 싫어서\n발표 전 불안감의 원인은 무엇일까?\n',
  'images': []},
 {'page': 6,
  'text': '최초의 발표하는 인공지능 모델 : 오인용\n01. 개요\n프로젝트 소개\n중요한 내용을 중심으로 발표용 대본 생성\nAI 음성 합성을 활용한 자동 발표 기능\n기능\n기업, 연구자, 학생 등